In [1]:
import statistics
from scipy import stats
import pandas as pd
import os
import math 
import numpy as np
parameters = pd.read_csv('pvalues.csv')
x = parameters.columns.tolist()
x[1] = 'samples'
parameters.columns = x

In [2]:
response = pd.read_csv('experimental.csv')


x = response['response'].tolist()
math = []
for string in x:
    if string == 'PD':
        math.append(-1)
    if string == 'PR':
        math.append(.5)
    if string == 'SD':
        math.append(0)
    if string == 'MR':
        math.append(0)
    if string == 'CR':
        math.append(1)   
response['data'] = math

response = response.sort_values(by = 'sample')
response

parameters = pd.read_csv('pvalues.csv')

x = parameters.columns.tolist()
x[1] = 'samples'
parameters.columns = x
parameters = parameters.sort_values(by = 'samples')
parameters



ref = list(parameters['samples'])
screen = list(response['sample'])
take_with =list(response['data'])

data_name = []
data_val = []

for x in response.index:
    if screen[x] in ref:
        data_name.append(screen[x])
        data_val.append(take_with[x])
info = pd.DataFrame(list(zip(data_name,data_val)), columns =['sample','exp'])
info

sample  exp
0      Patient1 -1.0
1     Patient10  0.5
2    Patient100  0.5
3    Patient102  0.0
4    Patient105  0.0
..          ...  ...
116    Patient9 -1.0
117   Patient94 -1.0
118   Patient96  1.0
119   Patient98 -1.0
120   Patient99  0.5

[121 rows x 2 columns]

In [3]:
parameters['exp'] = info['exp'].tolist()
parameters

Unnamed: 0     samples       A1BG  A1BG-AS1      A1CF         A2M  \
60           60    Patient1   0.130264  0.000000  0.065132  287.135293   
6             6   Patient10  10.049930  0.720561  0.000000  120.257841   
0             0  Patient100  19.614242  0.826789  0.035182  504.956774   
1             1  Patient102  20.075427  0.555721  0.208395  811.098196   
2             2  Patient105  13.009169  0.000000  0.000000  108.481865   
..          ...         ...        ...       ...       ...         ...   
107         107    Patient9  17.707440  0.802368  0.000000  102.620148   
103         103   Patient94  14.144119  0.775279  0.018909  329.531490   
104         104   Patient96  14.906180  1.336416  0.000000  290.516308   
105         105   Patient98  13.099469  1.236208  0.086751  873.109995   
106         106   Patient99  19.997280  0.815055  0.000000  727.882037   

      A2M-AS1     A2ML1   A3GALT2    A4GALT  ...      ZWINT      ZXDA  \
60   0.195397  0.423359  0.000000  0.162830  ...   2.540156  2.409891   
6    0.151697  0.132735  0.113773  1.365274  ...  25.409257  0.910182   
0    0.844380  0.228686  0.351825  8.215113  ...  10.695479  3.817301   
1    0.301016  0.000000  0.000000  2.315505  ...   6.506569  2.639676   
2    0.649106  0.054092  0.108184  0.567968  ...   7.708135  0.622060   
..        ...       ...       ...       ...  ...        ...       ...   
107  0.055336  0.249011  0.000000  2.434773  ...  18.454473  3.403149   
103  0.302548  2.930934  0.056728  1.096736  ...  60.944511  2.136745   
104  0.257003  0.205602  0.051401  0.308404  ...   1.028012  1.953224   
105  0.650636  0.065064  0.000000  1.084393  ...   8.545018  2.927862   
106  0.511779  0.151638  0.037910  1.459517  ...  15.069040  2.293527   

         ZXDB       ZXDC    ZYG11A     ZYG11B         ZYX      ZZEF1  \
60   2.116796   2.996081  0.032566   9.151074   20.972568  22.307778   
6    4.171669  10.391248  0.018962  20.573913   71.676859  17.862328   
0    3.008103  12.964750  0.527737  14.143363  204.832492  58.438126   
1    3.565877  13.568858  0.069465  27.786058  240.881970  36.006101   
2    2.028457   4.624881  0.054092  25.098771   20.014106  11.467542   
..        ...        ...       ...        ...         ...        ...   
107  4.426860  12.146197  0.000000  20.640235   90.473951  38.015660   
103  3.744031   9.624808  0.075637  22.445279   71.060959  28.326056   
104  2.672832   9.714717  0.000000  14.443574   57.825698  20.097643   
105  3.665249   9.065527  0.173503  19.497389   73.543544  38.582709   
106  2.615758   8.529645  0.018955  22.177078  126.238753  38.876229   

          ZZZ3  exp  
60   18.074185 -1.0  
6    14.487069  0.5  
0    12.947159  0.5  
1    16.277999  0.0  
2    33.428967  0.0  
..         ...  ...  
107  26.505824 -1.0  
103  18.606701 -1.0  
104  12.644553  1.0  
105  22.989135 -1.0  
106  20.774425  0.5  

[121 rows x 20851 columns]

In [4]:
pos = parameters.loc[parameters['exp'] > 0]
neg = parameters.loc[parameters['exp'] < 0]

In [6]:
import math
import statistics

ref = pos.columns.tolist()
ref.pop(0)
ref.pop(0)

fold = []
p_vals = []
for gene in ref:
    if gene != 'exp':
        positives = pos[gene].tolist()
        p_mean = statistics.mean(positives)
        negatives = neg[gene].tolist()
        n_mean = statistics.mean(negatives)
    
        if n_mean < 0:
            n_mean = 0
        if p_mean < 0:
            p_mean = 0
    
        fold.append(math.log2(p_mean+.0000001)-math.log2(n_mean+.0000001))
    
        t_p = stats.ttest_ind(positives, negatives)
        y = str(t_p).split("=")
        p = float(y[2].rstrip(')'))
        p_vals.append(-math.log(p, 10))

In [7]:
dat = pd.DataFrame(list(zip(ref,fold,p_vals)), columns =['Gene','log2 fold','p value'])

In [8]:
import plotly.graph_objects as go
fig = go.Figure(data=go.Scatter(x= dat['log2 fold'],
                                y=dat['p value'],
                                mode='markers',
                                marker = dict(color = 'Gray'), 
                                text=dat['Gene'].tolist(), showlegend = False))

significant = dat.loc[dat['p value'] >= 3.5]
significant2 =  dat.loc[dat['log2 fold'] >= 7]
significant3 =  dat.loc[dat['log2 fold'] <= -6]

fig.add_trace(go.Scatter(x= significant['log2 fold'],
                                y=significant['p value'],
                                mode='markers+text', textposition = 'top center',
                                marker = dict(color = 'Red'), 
                                text=significant['Gene'].tolist(), showlegend = False))
fig.add_trace(go.Scatter(x= significant2['log2 fold'],
                                y=significant2['p value'],
                                mode='markers+text', textposition = 'top right',
                                marker = dict(color = 'Red'), 
                                text=significant2['Gene'].tolist(), showlegend = False))
fig.add_trace(go.Scatter(x= significant3['log2 fold'],textposition = 'top left',
                                y=significant3['p value'],
                                mode='markers+text',
                                marker = dict(color = 'Red'), 
                                text=significant3['Gene'].tolist(), showlegend = False))



#ref = dat['Gene'].tolist().index('MMP9')
#diff = dat['log2 fold'].tolist()[ref]
#p = dat['p value'].tolist()[ref]
#fig.add_trace(go.Scatter(x=[diff], y=[p], mode='markers+text',text = "MMP9",name = "MMP9",textposition='top center', marker=dict(color='Blue', size = 15)))


#pos = parameters.loc[parameters['exp'] > 0]

fig.update_xaxes(title_text="log2 fold change")
fig.update_yaxes(title_text="-Log(P value)")
fig.update_xaxes(title_text="log2 fold Change")
fig.update_layout(template = "simple_white")
fig.update_layout(title_text = 'Comparative analysis: Progression vs. Response')
fig.update_xaxes(range=[-10, 10])
fig.show()


In [ ]:
fig.write_image('progress_vs_response_rna_expression.png',width=800, height=600, scale=1)
